In [113]:
import xml.etree.ElementTree as Xet
import pandas as pd
import numpy as np
import geopandas as gpd
import os
import matplotlib.pyplot as plt
import warnings
import re

# Ignore all warnings
warnings.filterwarnings('ignore')

In [114]:
# Read in the GeoJSON file
kansas_2022 = './ks_2022g (1)/ks_2022g.shp'
gdf_kansan_2022 = gpd.read_file(kansas_2022)
gdf_kansan_2022.head(5)

COUNTYFP   VTDST                                NAMELSAD  REG_DEM  REG_REP  \
0      001  000010        Carlyle Township Voting District       28      165   
1      001  000020  Cottage Grove Township Voting District       19      108   
2      001  000030     Deer Creek Township Voting District       11       65   
3      001  00006A       Humboldt Township Voting District       29      127   
4      001  170040                             Iola Ward 4      169      366   

   REG_UNA  REG_LIB  REG_TOTAL  G22USSRMOR  G22USSDHOL  ...  G22SSC2NO  \
0       42        0        235         104          19  ...         53   
1       43        1        171          72          16  ...         48   
2       17        1         94          44           7  ...         16   
3       53        2        211         104          15  ...         42   
4      303        8        846         210         119  ...         93   

   G22SSC3YES  G22SSC3NO  G22SSC5YES  G22SSC5NO  G22SSC6YES  G22SSC6NO  \
0          66         56          67         55          65         57   
1          29         49          36         42          33         45   
2          28         19          29         18          30         17   
3          60         43          59         43          63         39   
4         228         94         232         90         226         93   

   G22SSC7YES  G22SSC7NO                                           geometry  
0          72         48  POLYGON Z ((-95.42748 37.96487 0.00000, -95.42...  
1          44         34  POLYGON Z ((-95.46656 37.75217 0.00000, -95.46...  
2          31         15  POLYGON Z ((-95.33574 37.98185 0.00000, -95.33...  
3          61         38  POLYGON Z ((-95.47322 37.84735 0.00000, -95.47...  
4         224         93  POLYGON Z ((-95.40017 37.90415 0.00000, -95.40...  

[5 rows x 38 columns]

In [115]:
len(gdf_kansan_2022)

4379

In [116]:
gdf_kansan_2022.columns

Index(['COUNTYFP', 'VTDST', 'NAMELSAD', 'REG_DEM', 'REG_REP', 'REG_UNA',
       'REG_LIB', 'REG_TOTAL', 'G22USSRMOR', 'G22USSDHOL', 'G22USSLGRA',
       'G22GOVDKEL', 'G22GOVRSCH', 'G22GOVIPYL', 'G22GOVLCOR', 'G22SOSRSCH',
       'G22SOSDREP', 'G22SOSLLAN', 'G22ATGRKOB', 'G22ATGDMAN', 'G22TRERJOH',
       'G22TREDROG', 'G22TRELROB', 'G22INSRSCH', 'G22INSDCOR', 'G22SSC1YES',
       'G22SSC1NO', 'G22SSC2YES', 'G22SSC2NO', 'G22SSC3YES', 'G22SSC3NO',
       'G22SSC5YES', 'G22SSC5NO', 'G22SSC6YES', 'G22SSC6NO', 'G22SSC7YES',
       'G22SSC7NO', 'geometry'],
      dtype='object')

Still need: Kansas senate, Kansas House of representatives, Constitutional Amendment Rules and Regulations, Sheriff Election and Recall, Turnout information?

### Kansas Senate: state senates are elected at year 2020, 2024..., not in 2022 general election

In [117]:

senate_csv_path = './2022-General-Election-Kansas-Senate-Results-By-Precinct.xlsx'

all_sheets = pd.read_excel(senate_csv_path, sheet_name=None)

print("Sheet names:", all_sheets.keys())

for sheet_name, df in all_sheets.items():
    print(f"Processing sheet: {sheet_name}")
    display(df.head()) 


Sheet names: dict_keys(['KS Senate'])
Processing sheet: KS Senate


County           Precinct              Race              Candidate  \
0  Clark  Appleton Township  Kansas Senate 38             Lara, Jose   
1  Clark  Appleton Township  Kansas Senate 38  Ryckman Sr, Ronald W.   
2  Clark           Center 1  Kansas Senate 38             Lara, Jose   
3  Clark           Center 1  Kansas Senate 38  Ryckman Sr, Ronald W.   
4  Clark           Center 2  Kansas Senate 38             Lara, Jose   

        Party  Votes     VTD  
0  Democratic     30  000010  
1  Republican    282  000010  
2  Democratic     27  000020  
3  Republican    189  000020  
4  Democratic     18  000030

### Read in county fips for better matching

In [118]:

county_fips_path = './US_FIPS_Codes (1).xls'

county_fip = pd.read_excel(county_fips_path)
kansas_fip = county_fip[county_fip['U.S. FIPS County Codes'] == 'Kansas']

kansas_fip.drop(columns=['U.S. FIPS County Codes', 'Unnamed: 2'], inplace=True)
kansas_fip.rename(columns={'Unnamed: 3': 'CountyFP'}, inplace=True)
kansas_fip.rename(columns={'Unnamed: 1': 'COUNTYNA'}, inplace=True)
kansas_fip


COUNTYNA CountyFP
886         Allen      001
887      Anderson      003
888      Atchison      005
889        Barber      007
890        Barton      009
891       Bourbon      011
892         Brown      013
893        Butler      015
894         Chase      017
895    Chautauqua      019
896      Cherokee      021
897      Cheyenne      023
898         Clark      025
899          Clay      027
900         Cloud      029
901        Coffey      031
902      Comanche      033
903        Cowley      035
904      Crawford      037
905       Decatur      039
906     Dickinson      041
907      Doniphan      043
908       Douglas      045
909       Edwards      047
910           Elk      049
911         Ellis      051
912     Ellsworth      053
913        Finney      055
914          Ford      057
915      Franklin      059
916         Geary      061
917          Gove      063
918        Graham      065
919         Grant      067
920          Gray      069
921       Greeley      071
922     Greenwood      073
923      Hamilton      075
924        Harper      077
925        Harvey      079
926       Haskell      081
927      Hodgeman      083
928       Jackson      085
929     Jefferson      087
930        Jewell      089
931       Johnson      091
932        Kearny      093
933       Kingman      095
934         Kiowa      097
935       Labette      099
936          Lane      101
937   Leavenworth      103
938       Lincoln      105
939          Linn      107
940         Logan      109
941          Lyon      111
942     McPherson      113
943        Marion      115
944      Marshall      117
945         Meade      119
946         Miami      121
947      Mitchell      123
948    Montgomery      125
949        Morris      127
950        Morton      129
951        Nemaha      131
952        Neosho      133
953          Ness      135
954        Norton      137
955         Osage      139
956       Osborne      141
957        Ottawa      143
958        Pawnee      145
959      Phillips      147
960  Pottawatomie      149
961         Pratt      151
962       Rawlins      153
963          Reno      155
964      Republic      157
965          Rice      159
966         Riley      161
967         Rooks      163
968          Rush      165
969       Russell      167
970        Saline      169
971         Scott      171
972      Sedgwick      173
973        Seward      175
974       Shawnee      177
975      Sheridan      179
976       Sherman      181
977         Smith      183
978      Stafford      185
979       Stanton      187
980       Stevens      189
981        Sumner      191
982        Thomas      193
983         Trego      195
984     Wabaunsee      197
985       Wallace      199
986    Washington      201
987       Wichita      203
988        Wilson      205
989       Woodson      207
990     Wyandotte      209

The original PBER only has a County FP column, so I add a county name column to PBER

In [119]:
merged_df = pd.merge(gdf_kansan_2022, kansas_fip, left_on='COUNTYFP', right_on='CountyFP', how='outer', indicator=True)
merged_df.head(5)


COUNTYFP   VTDST                                NAMELSAD  REG_DEM  REG_REP  \
0      001  000010        Carlyle Township Voting District       28      165   
1      001  000020  Cottage Grove Township Voting District       19      108   
2      001  000030     Deer Creek Township Voting District       11       65   
3      001  00006A       Humboldt Township Voting District       29      127   
4      001  170040                             Iola Ward 4      169      366   

   REG_UNA  REG_LIB  REG_TOTAL  G22USSRMOR  G22USSDHOL  ...  G22SSC5YES  \
0       42        0        235         104          19  ...          67   
1       43        1        171          72          16  ...          36   
2       17        1         94          44           7  ...          29   
3       53        2        211         104          15  ...          59   
4      303        8        846         210         119  ...         232   

   G22SSC5NO  G22SSC6YES  G22SSC6NO  G22SSC7YES  G22SSC7NO  \
0         55          65         57          72         48   
1         42          33         45          44         34   
2         18          30         17          31         15   
3         43          63         39          61         38   
4         90         226         93         224         93   

                                            geometry  COUNTYNA  CountyFP  \
0  POLYGON Z ((-95.42748 37.96487 0.00000, -95.42...     Allen       001   
1  POLYGON Z ((-95.46656 37.75217 0.00000, -95.46...     Allen       001   
2  POLYGON Z ((-95.33574 37.98185 0.00000, -95.33...     Allen       001   
3  POLYGON Z ((-95.47322 37.84735 0.00000, -95.47...     Allen       001   
4  POLYGON Z ((-95.40017 37.90415 0.00000, -95.40...     Allen       001   

   _merge  
0    both  
1    both  
2    both  
3    both  
4    both  

[5 rows x 41 columns]

In [120]:
pber_county_counts = merged_df['COUNTYNA'].value_counts().reset_index()
pber_county_counts.columns = ['COUNTYNA', 'Count']
pber_county_counts

COUNTYNA  Count
0         Johnson    610
1        Sedgwick    518
2         Shawnee    248
3       Wyandotte    144
4         Douglas    116
5          Saline     94
6            Reno     86
7      Montgomery     84
8           Riley     81
9           Miami     75
10         Cowley     73
11         Finney     71
12         Butler     67
13    Leavenworth     63
14       Crawford     62
15           Lyon     61
16          Geary     59
17       Cherokee     51
18         Barton     51
19         Sumner     50
20           Ford     47
21        Labette     45
22         Harvey     43
23          Ellis     42
24         Nemaha     37
25      Dickinson     36
26         Neosho     36
27         Marion     35
28      McPherson     34
29          Cloud     34
30         Pawnee     33
31   Pottawatomie     31
32       Marshall     31
33        Osborne     30
34        Kingman     30
35         Wilson     29
36       Phillips     29
37     Washington     29
38        Bourbon     29
39        Decatur     28
40          Brown     28
41          Smith     28
42       Franklin     27
43           Rice     27
44       Atchison     27
45       Republic     26
46          Allen     26
47         Jewell     25
48      Ellsworth     25
49           Clay     25
50       Mitchell     25
51          Osage     25
52        Jackson     24
53        Lincoln     24
54       Stafford     24
55         Ottawa     24
56         Thomas     23
57         Seward     23
58         Barber     22
59         Coffey     21
60         Harper     21
61      Greenwood     20
62        Sherman     19
63         Morris     19
64        Russell     19
65         Graham     18
66       Anderson     18
67        Rawlins     17
68          Pratt     17
69       Hodgeman     16
70      Wabaunsee     15
71      Jefferson     15
72       Sheridan     15
73     Chautauqua     14
74          Rooks     14
75        Edwards     13
76       Doniphan     13
77           Linn     13
78           Rush     13
79          Trego     12
80         Norton     12
81          Logan     12
82       Hamilton     12
83        Haskell     11
84          Chase     11
85        Woodson     11
86           Ness     11
87        Stevens     11
88          Scott     11
89            Elk     10
90         Morton     10
91           Gove      9
92         Kearny      9
93          Meade      9
94           Gray      8
95       Cheyenne      8
96          Clark      7
97           Lane      6
98          Grant      5
99          Kiowa      5
100      Comanche      5
101       Wallace      5
102       Stanton      3
103       Wichita      3
104       Greeley      3

### Kansas House

The election result is an excel file with 5 different sheet. The first sheet Kansas2022 has results for 101 counites, and 4 other sheets have results for the other 4 counties with a large number of precincts

In [121]:
house_csv_path = './2022-General-Election-Kansas-House-of-Representatives-Results-By-Precinct.xlsx'

all_sheets = pd.read_excel(house_csv_path, sheet_name=None)

print("Sheet names:", all_sheets.keys())

dfs = {}  # Dictionary to store each DataFrame

for sheet_name, df in all_sheets.items():
    dfs[sheet_name] = df  # Assign each DataFrame to the dictionary

    print(f"Processing sheet: {sheet_name}")
    display(df) 


Sheet names: dict_keys(['KSHouse', 'JOHNSON', 'SEDGWICK', 'SHAWNEE', 'WYANDOTTE'])
Processing sheet: KSHouse


County                                       Precinct  \
0            Allen                               Carlyle Township   
1            Allen                               Carlyle Township   
2            Allen                         Cottage Grove Township   
3            Allen                         Cottage Grove Township   
4            Allen                            Deer Creek Township   
5            Allen                            Deer Creek Township   
6            Allen                                       East Elm   
7            Allen                                       East Elm   
8            Allen                                Geneva Township   
9            Allen                                Geneva Township   
10           Allen                              Humboldt Township   
11           Allen                              Humboldt Township   
12           Allen                Humboldt Township Rural Enclave   
13           Allen                Humboldt Township Rural Enclave   
14           Allen                        Humboldt Township Split   
15           Allen                        Humboldt Township Split   
16           Allen             Humboldt Township Rural Enclave 2x   
17           Allen             Humboldt Township Rural Enclave 2x   
18           Allen                                Humboldt Ward 1   
19           Allen                                Humboldt Ward 1   
20           Allen                                Humboldt Ward 2   
21           Allen                                Humboldt Ward 2   
22           Allen                                 Logan Township   
23           Allen                                 Logan Township   
24           Allen                              Marmaton Township   
25           Allen                              Marmaton Township   
26           Allen                                  North Elsmore   
27           Allen                                  North Elsmore   
28           Allen                              North Iola Part A   
29           Allen                              North Iola Part A   
30           Allen                              North Iola Part B   
31           Allen                              North Iola Part B   
32           Allen                                 Osage Township   
33           Allen                                 Osage Township   
34           Allen                                 Salem Township   
35           Allen                                 Salem Township   
36           Allen                                  South Elsmore   
37           Allen                                  South Elsmore   
38           Allen                                     South Iola   
39           Allen                                     South Iola   
40           Allen                             South Iola Enclave   
41           Allen                             South Iola Enclave   
42           Allen                           Bassett City Enclave   
43           Allen                           Bassett City Enclave   
44           Allen                                       West Elm   
45           Allen                                       West Elm   
46           Allen                                    Iola Ward 1   
47           Allen                                    Iola Ward 1   
48           Allen                                    Iola Ward 2   
49           Allen                                    Iola Ward 2   
50           Allen                                    Iola Ward 3   
51           Allen                                    Iola Ward 3   
52           Allen                            Iola Ward 3 Enclave   
53           Allen                            Iola Ward 3 Enclave   
54           Allen                            Iola Ward 3 Exclave   
55           Allen                            Iola Ward 3 Exclave   
56           Allen                                    Iola Ward 4   
57        

Processing sheet: JOHNSON


PRECINCT CODE                       PRECINCT NAME     VTD Unnamed: 3  \
0             NaN                                 NaN     NaN        NaN   
1               1          Aubry Township Precinct 01      10       1001   
2               2          Aubry Township Precinct 02      20       1002   
3               3          Aubry Township Precinct 03  220010       1003   
4               4          Aubry Township Precinct 04      40       1004   
5               5          Aubry Township Precinct 05  900010       1005   
6               6          Aubry Township Precinct 06  900020       1006   
7               7          Aubry Township Precinct 07  920520       1007   
8               8          Aubry Township Precinct 08  220000       1008   
9               9        Gardner Township Precinct 01  221320       2001   
10             10        Gardner Township Precinct 02  221280       2002   
11             11        Gardner Township Precinct 03  900150       2003   
12             12        Gardner Township Precinct 04  900160       2004   
13             13        Gardner Township Precinct 05  921070       2005   
14             14        Gardner Township Precinct 06  92043A       2006   
15             15        Gardner Township Precinct 07  900170       2007   
16             16        Gardner Township Precinct 08  900180       2008   
17             17        Gardner Township Precinct 09  920410       2009   
18             18         Gardner Township Precinct10  170080       2010   
19             19         Gardner Township Precinct11  221550       2011   
20             20         Gardner Township Precinct12  920420       2012   
21             21         Gardner Township Precinct13  920470       2013   
22             22         Gardner Township Precinct14  921080       2014   
23             23         Gardner Township Precinct15  190050       2015   
24             24         Gardner Township Precinct16  190060       2016   
25             25         Gardner Township Precinct17  190070       2017   
26             26         Gardner Township Precinct18  190080       2018   
27             27         Gardner Township Precinct19  221310       2019   
28             28         Gardner Township Precinct20  190090       2020   
29             29         Gardner Township Precinct21  200030       2021   
30             30         Gardner Township Precinct22  200040       2022   
31             31         Gardner Township Precinct23  210000       2023   
32             32         Gardner Township Precinct24  210010       2024   
33             33         Gardner Township Precinct25  221270       2025   
34             34         Gardner Township Precinct26  221540       2026   
35             35         Gardner Township Precinct27  221780       2027   
36             36      Lexington Township Precinct 01  221300       3001   
37             37      Lexington Township Precinct 02    4070       3002   
38             38      Lexington Township Precinct 03    4080       3003   
39             39      Lexington Township Precinct 04    4090       3004   
40             40      Lexington Township Precinct 05    4100       3005   
41             41      Lexington Township Precinct 06  210020       3006   
42             42      Lexington Township Precinct 07  221790       3007   
43             43      Lexington Township Precinct 08  221800       3008   
44             44      Lexington Township Precinct 09  221290       3009   
45             45       McCamish Township Precinct 01  221430       4001   
46             46       McCamish Township Precinct 02  221450       4002   
47             47       McCamish Township Precinct 03  920390       4003   
48             48       McCamish Township Precinct 04  100040       4004   
49             49       McCamish Township Precinct 05  200050       4005   
50             50       McCamish Township Precinct 06  221420       4006   
51             51       McCamish Township Precinct 0

Processing sheet: SEDGWICK


PRECINCT CODE  PRECINCT NAME State Representative 72nd District  \
0             NaN            NaN                 REP Avery Anderson   
1               1            101                                  0   
2               2            102                                  0   
3               3            103                                  0   
4               4            104                                  0   
5               5            105                                  0   
6               6            106                                  0   
7               7            107                                  0   
8               8            108                                  0   
9               9            109                                  0   
10             10            110                                  0   
11             11            111                                  0   
12             12            112                                  0   
13             13            113                                  0   
14             14            114                                  0   
15             15            116                                  0   
16             16            117                                  0   
17             17            118                                  0   
18             18            119                                  0   
19             19            120                                  0   
20             20            121                                  0   
21             21            122                                  0   
22             22            123                                  0   
23             23            124                                  0   
24             24            126                                  0   
25             25            127                                  0   
26             26            128                                  0   
27             27            129                                  0   
28             28            130                                  0   
29             29            133                                  0   
30             30            135                                  0   
31             31            136                                  0   
32             32            205                                  0   
33             33            206                                  0   
34             34            207                                  0   
35             35            208                                  0   
36             36            209                                  0   
37             37            210                                  0   
38             38            211                                  0   
39             39            212                                  0   
40             40            213                                  0   
41             41            214                                  0   
42             42            215                                  0   
43             43            216                                  0   
44             44            217                                  0   
45             45            218                                  0   
46             46            221                                  0   
47             47            222                                  0   
48             48            223                                  0   
49             49            224                                  0   
50             50            225                                  0   
51             51            226                                  0   
52             52            227                                  0   
53             53            228                                  0   
54             54            230                                  0   
55             55           

Processing sheet: SHAWNEE


PRECINCT CODE          PRECINCT NAME  \
0             NaN                    NaN   
1               1       1 East Rossville   
2               2       2 West Rossville   
3               9     9 East Silver Lake   
4              10    10 West Silver Lake   
5              12               12 Grove   
6              14                14 Kiro   
7              15      15 Messhoss Creek   
8              16             16 SE Kiro   
9              17               17 Croco   
10             18            18 Flathead   
11             22  22 Little Muddy Creek   
12             23                23 Coup   
13             24                 24 Sac   
14             25             25 Sherman   
15             26            26 Iroquois   
16             27             27 Halfday   
17             28        28 West Wichita   
18             29           29 Indianola   
19             30              30 Apache   
20             31        31 East Wichita   
21             32                 32 Fox   
22             33              33 Elmont   
23             34              34 Kilmer   
24             35           35 Rochester   
25             36        36 East Soldier   
26             37           37 Whitfield   
27             38               38 Sioux   
28             39        39 Pottawatomie   
29             40       40 Stinson Creek   
30             41      41 North Tecumseh   
31             42      42 South Tecumseh   
32             43              43 Pawnee   
33             44                 44 Kaw   
34             45                45 Peck   
35             46           46 East Peck   
36             47               47 Kiowa   
37             48            48 Cheyenne   
38             49               49 Ponca   
39             50        50 North Potter   
40             51             51 Channel   
41             52          52 Deer Creek   
42             53             53 Pauline   
43             54         54 West Potter   
44             55     55 Central Pauline   
45             56         56 NW Monmouth   
46             57         57 NE Monmouth   
47             58      58 South Monmouth   
48             59         59 NC Monmouth   
49             61      61 Sixty-First St   
50             62              62 Forbes   
51             63             63 Montara   
52             64              64 Cullen   
53             65            65 Wakarusa   
54             66            66 Kingston   
55             72      72 City Of Auburn   
56             73          73 Meadowlark   
57             74             74 Buffalo   
58             78           78 Hodges Rd   
59             79    79 North Gaillardia   
60             80          80 Gaillardia   
61             81               81 Dover   
62             82             82 Willard   
63             83    83 Ichabod Washburn   
64             84               84 Yucca   
65             85          85 Aldersgate   
66             86           86 Sunflower   
67             87            87 Washburn   
68             88              88 Lykins   
69             89       89 North Mission   
70             90       90 South Mission   
71             91     91 Central Mission   
72             92            92 Sherwood   
73             93      93 South Sherwood   
74             94        94 Indian Hills   
75             95                95 York   
76             96             96 Vaquero   
77             97          97 York Outer   
78             98          98 NE Mission   
79             99             99 Verbena   
80            101      Ward 1 Precinct 1   
81            102      Ward 1 Precinct 2   
82            103      Ward 1 Precinct 3   
83            104      Ward 1 Precinct 4   
84            105      Ward 1 Precinct 5   
85            106      Ward 1 Precinct 6   
86            107      Ward 1 Precinct 7   
87            108      Ward 1 Precinct 8   
88            109      Ward 1 Precinct 9   
89            110     Ward 1 Precinct 10   


Processing sheet: WYANDOTTE


PRECINCT CODE  PRECINCT NAME For State Representative 31st District  \
0             NaN            NaN                     REP Dennis Grindel   
1               1        BS01-01                                      0   
2               2        BS02-01                                      0   
3               3        BS03-01                                      0   
4               4        BS04-01                                      0   
5               5        DW01-01                                      0   
6               6        ED01-01                                      0   
7               7        ED02-01                                      0   
8               8        ED02-02                                      0   
9               9        KC01-01                                      0   
10             10        KC01-02                                      0   
11             11        KC01-03                                      0   
12             12        KC01-04                                      0   
13             13        KC01-05                                      0   
14             14        KC02-01                                      0   
15             15        KC02-02                                      0   
16             16        KC02-03                                      0   
17             17        KC02-04                                      0   
18             18        KC02-05                                      0   
19             19        KC02-06                                      0   
20             20        KC02-07                                      0   
21             21        KC03-01                                      0   
22             22        KC03-02                                      0   
23             23        KC03-03                                      0   
24             24        KC03-04                                      0   
25             25        KC03-05                                      0   
26             26        KC04-01                                      0   
27             27        KC04-02                                      0   
28             28        KC04-03                                      0   
29             29        KC04-04                                      0   
30             30        KC05-01                                      0   
31             31        KC05-02                                      0   
32             32        KC05-03                                      0   
33             33        KC05-04                                      0   
34             34        KC05-05                                      0   
35             35        KC06-01                                      0   
36             36        KC06-02                                      0   
37             37        KC07-01                                     62   
38             38        KC07-02                                     31   
39             39        KC07-03                                     42   
40             40        KC07-04                                      0   
41             41        KC07-05                                     16   
42             42        KC07-06                                     94   
43             43        KC07-07                                     33   
44             44        KC07-08                                     72   
45             45        KC07-09                                      0   
46             46        KC07-10                                      0   
47             47        KC07-11                                      0   
48             48        KC07-12                                      0   
49             49        KC08-01                                     45   
50             50        KC08-02                                     54   
51             51        KC08-03                                     96   
52             52        KC08

Count how many precints each county has.

In [122]:
KSHouse = dfs['KSHouse']
JOHNSON_COUNTY = dfs['JOHNSON']
SEDGWICK_COUNTY = dfs['SEDGWICK']
SHAWNEE_COUNTY = dfs['SHAWNEE']
WYANDOTTE_COUNTY = dfs['WYANDOTTE']

In [123]:
unique_combinations = KSHouse[['County', 'Precinct']].drop_duplicates()
len(unique_combinations)

3144

In [124]:
election_county_counts = KSHouse['County'].value_counts().reset_index()
election_county_counts.columns = ['County', 'Count']
election_county_counts

County  Count
0         Douglas    194
1           Riley    178
2           Miami    167
3            Reno    147
4      Montgomery    138
5     Leavenworth    136
6          Saline    134
7        Cherokee    106
8          Sumner    106
9          Cowley    101
10         Butler     95
11          Geary     92
12           Lyon     85
13         Harvey     85
14          Ellis     83
15         Finney     71
16       Crawford     67
17          Osage     62
18          Allen     62
19        Osborne     60
20          Cloud     60
21          Smith     58
22        Labette     58
23           Rice     54
24         Pawnee     54
25           Ford     54
26           Clay     54
27       Franklin     53
28        Lincoln     52
29       Anderson     50
30      Ellsworth     50
31      Dickinson     50
32         Marion     48
33         Barber     48
34       Stafford     48
35         Barton     46
36         Coffey     46
37      McPherson     45
38         Harper     44
39         Neosho     43
40        Russell     40
41         Morris     38
42       Marshall     36
43          Pratt     35
44        Bourbon     31
45         Wilson     31
46       Mitchell     31
47         Nemaha     30
48   Pottawatomie     30
49        Kingman     29
50     Washington     29
51          Brown     28
52       Phillips     28
53        Decatur     28
54       Republic     27
55       Atchison     27
56        Jackson     26
57           Rush     26
58         Thomas     25
59         Jewell     25
60         Seward     24
61         Ottawa     24
62         Graham     21
63      Greenwood     21
64        Sherman     20
65        Rawlins     19
66        Stevens     17
67       Hodgeman     16
68      Jefferson     15
69      Wabaunsee     15
70       Sheridan     15
71           Linn     14
72     Chautauqua     14
73          Rooks     14
74        Edwards     13
75       Doniphan     13
76         Norton     12
77       Comanche     12
78       Hamilton     12
79          Logan     12
80          Trego     11
81          Scott     11
82        Woodson     11
83        Haskell     11
84          Chase     11
85           Ness     11
86         Morton     10
87           Lane     10
88          Kiowa     10
89            Elk     10
90         Kearny      9
91          Meade      9
92           Gove      9
93           Gray      8
94       Cheyenne      8
95          Clark      7
96          Grant      6
97        Wallace      5
98        Stanton      3
99        Greeley      3
100       Wichita      3

In [125]:
unique_combinations1 = JOHNSON_COUNTY[['PRECINCT CODE', 'PRECINCT NAME']].drop_duplicates()
unique_combinations2 = SEDGWICK_COUNTY[['PRECINCT CODE', 'PRECINCT NAME']].drop_duplicates()
unique_combinations3 = SHAWNEE_COUNTY[['PRECINCT CODE', 'PRECINCT NAME']].drop_duplicates()
unique_combinations4 = WYANDOTTE_COUNTY[['PRECINCT CODE', 'PRECINCT NAME']].drop_duplicates()

len(unique_combinations1) + len(unique_combinations2) + len(unique_combinations3) + len(unique_combinations4)

1394

The total number of precincts from Official Kansas election result is 3144 + 1394 = 4538, which is different from 4379 from PBER from IKE Lab. This means that additional investigations have to be made.

Create a table to display the differences in the number of counites for the 2 datasets.

In [126]:
pd.set_option('display.max_rows', None)

merged_counts = pd.merge(pber_county_counts, election_county_counts, left_on='COUNTYNA', right_on='County', how='outer', indicator=True)

merged_counts


COUNTYNA  Count_x        County  Count_y     _merge
0         Johnson      610           NaN      NaN  left_only
1        Sedgwick      518           NaN      NaN  left_only
2         Shawnee      248           NaN      NaN  left_only
3       Wyandotte      144           NaN      NaN  left_only
4         Douglas      116       Douglas    194.0       both
5          Saline       94        Saline    134.0       both
6            Reno       86          Reno    147.0       both
7      Montgomery       84    Montgomery    138.0       both
8           Riley       81         Riley    178.0       both
9           Miami       75         Miami    167.0       both
10         Cowley       73        Cowley    101.0       both
11         Finney       71        Finney     71.0       both
12         Butler       67        Butler     95.0       both
13    Leavenworth       63   Leavenworth    136.0       both
14       Crawford       62      Crawford     67.0       both
15           Lyon       61          Lyon     85.0       both
16          Geary       59         Geary     92.0       both
17       Cherokee       51      Cherokee    106.0       both
18         Barton       51        Barton     46.0       both
19         Sumner       50        Sumner    106.0       both
20           Ford       47          Ford     54.0       both
21        Labette       45       Labette     58.0       both
22         Harvey       43        Harvey     85.0       both
23          Ellis       42         Ellis     83.0       both
24         Nemaha       37        Nemaha     30.0       both
25      Dickinson       36     Dickinson     50.0       both
26         Neosho       36        Neosho     43.0       both
27         Marion       35        Marion     48.0       both
28      McPherson       34     McPherson     45.0       both
29          Cloud       34         Cloud     60.0       both
30         Pawnee       33        Pawnee     54.0       both
31   Pottawatomie       31  Pottawatomie     30.0       both
32       Marshall       31      Marshall     36.0       both
33        Osborne       30       Osborne     60.0       both
34        Kingman       30       Kingman     29.0       both
35         Wilson       29        Wilson     31.0       both
36       Phillips       29      Phillips     28.0       both
37     Washington       29    Washington     29.0       both
38        Bourbon       29       Bourbon     31.0       both
39        Decatur       28       Decatur     28.0       both
40          Brown       28         Brown     28.0       both
41          Smith       28         Smith     58.0       both
42       Franklin       27      Franklin     53.0       both
43           Rice       27          Rice     54.0       both
44       Atchison       27      Atchison     27.0       both
45       Republic       26      Republic     27.0       both
46          Allen       26         Allen     62.0       both
47         Jewell       25        Jewell     25.0       both
48      Ellsworth       25     Ellsworth     50.0       both
49           Clay       25          Clay     54.0       both
50       Mitchell       25      Mitchell     31.0       both
51          Osage       25         Osage     62.0       both
52        Jackson       24       Jackson     26.0       both
53        Lincoln       24       Lincoln     52.0       both
54       Stafford       24      Stafford     48.0       both
55         Ottawa       24        Ottawa     24.0       both
56         Thomas       23        Thomas     25.0       both
57         Seward       23        Seward     24.0       both
58         Barber       22        Barber     48.0       both
59         Coffey       21        Coffey     46.0       both
60         Harper       21        Harper     44.0       both
61      Greenwood       20     Greenwood     21.0       both
62        Sherman       19       Sherman     20.0       both
63         Morris       19        Morris     38.0       both
64        Russell       19       Russell    

### Process 104 counties

Using a similar approach to create column names and pivot

In [127]:
election_results_cleaned = KSHouse

# Extract district number from the 'Race' column and create new column
election_results_cleaned['District'] = election_results_cleaned['Race'].str.extract(r'(\d+)', expand=False)

# Function to create a unique column name based on the office, district, candidate, and party
def create_column_name(row):
    office_abbr = "SL"  # Abbreviation for State Legislature
    party_initial = row['Party'][0]
    last_name = row['Candidate'].split()[0][:3].upper()
    district = row['District'].zfill(3)  # Ensure the district number has leading zeros
    
    # Create a unique column name that includes office, district, candidate, and party
    unique_name = f"{office_abbr}{district}{party_initial}{last_name}"
    
    return unique_name

# Apply the function to generate a unique column name for each candidate
election_results_cleaned['ColumnName'] = election_results_cleaned.apply(create_column_name, axis=1)

# Pivot dataset so that each column represents a candidate (unique column name) and each row represents a precinct
pivoted_df = election_results_cleaned.pivot_table(
    index=['County', 'Precinct', 'VTD'],
    columns='ColumnName',
    values='Votes',
    aggfunc='sum'
)

# Flatten the columns
pivoted_df.columns = [col for col in pivoted_df.columns]

# Reset index
pivoted_df.reset_index(inplace=True)

# Display the final DataFrame
pivoted_df.head(5)

County                Precinct     VTD  SL001DROG  SL001RHOU  SL002RCOL  \
0  Allen    Bassett City Enclave  00020C        NaN        NaN        NaN   
1  Allen        Carlyle Township  000010        NaN        NaN        NaN   
2  Allen  Cottage Grove Township  000020        NaN        NaN        NaN   
3  Allen     Deer Creek Township  000030        NaN        NaN        NaN   
4  Allen                East Elm  000040        NaN        NaN        NaN   

   SL003RSMI  SL004RJAC  SL005RBAR  SL006DFRI  ...  SL116RHOF  SL117DTRI  \
0        NaN        NaN        NaN        NaN  ...        NaN        NaN   
1        NaN        NaN        NaN        NaN  ...        NaN        NaN   
2        NaN        NaN        NaN        NaN  ...        NaN        NaN   
3        NaN        NaN        NaN        NaN  ...        NaN        NaN   
4        NaN        NaN        NaN        NaN  ...        NaN        NaN   

   SL117RTUR  SL118RMIN  SL119RGOE  SL120RSMI  SL122RCLI  SL123RLEW  \
0        NaN        NaN        NaN        NaN        NaN        NaN   
1        NaN        NaN        NaN        NaN        NaN        NaN   
2        NaN        NaN        NaN        NaN        NaN        NaN   
3        NaN        NaN        NaN        NaN        NaN        NaN   
4        NaN        NaN        NaN        NaN        NaN        NaN   

   SL124RYOU  SL125RFRA  
0        NaN        NaN  
1        NaN        NaN  
2        NaN        NaN  
3        NaN        NaN  
4        NaN        NaN  

[5 rows x 101 columns]

In [128]:
matching_combinations = pd.merge(
    merged_df[['COUNTYNA', 'VTDST']], 
    pivoted_df[['County', 'VTD']],    
    left_on=['COUNTYNA', 'VTDST'],     
    right_on=['County', 'VTD'],        
    how='inner'                        
)

# Count the number of matching combinations
num_matching_combinations = len(matching_combinations)
num_matching_combinations

2371

There are only 2371 out of 3144 precincts that match, indicating there needs more processing

Check that after pivoting, the numbers match previous results(they did)

In [129]:
def check_total_votes_after_pivot(df, original_df):
    # Reset index to ensure columns are in the correct place
    df.reset_index(inplace=True)

    candidate_totals = {}
    
    for column in df.columns:
        if column not in ['County', 'Precinct', 'VTD']:
            candidate_totals[column] = df[column].sum()

    # Print the total votes for each candidate
    print("\nTotal Votes for Each Candidate by Office After Pivoting:")
    for candidate, total_votes in candidate_totals.items():
        print(f"{candidate}: {total_votes}")
    
    # Compare with the original DataFrame
    print("\nValidation against original DataFrame:")
    original_totals = original_df.groupby('ColumnName')['Votes'].sum()
    print(original_totals)

# Call the function to check totals after pivoting
check_total_votes_after_pivot(pivoted_df, election_results_cleaned)



Total Votes for Each Candidate by Office After Pivoting:
index: 4937653
SL001DROG: 1928.0
SL001RHOU: 5847.0
SL002RCOL: 6566.0
SL003RSMI: 4714.0
SL004RJAC: 7069.0
SL005RBAR: 5705.0
SL006DFRI: 2954.0
SL006RPOE: 6265.0
SL007RGOD: 5789.0
SL009DCLO: 2127.0
SL009RGAR: 6101.0
SL010DHAS: 6695.0
SL011DWIL: 1712.0
SL011RBRY: 5104.0
SL012RBLE: 7674.0
SL013RNEW: 7742.0
SL026DTIF: 305.0
SL026RTHO: 638.0
SL038RJOH: 7322.0
SL040DALL: 3222.0
SL040RBUE: 3999.0
SL041DSCH: 2180.0
SL041RPRO: 2324.0
SL042RNEE: 6705.0
SL043DDAV: 82.0
SL043RSUT: 169.0
SL044DBAL: 8890.0
SL045DAMY: 9613.0
SL046DHIG: 5715.0
SL047RELL: 7819.0
SL051RTIT: 7702.0
SL054DJOH: 881.0
SL054RCOR: 2288.0
SL059DMCC: 2937.0
SL059RSCH: 5344.0
SL060DMCG: 2953.0
SL060RSCH: 3649.0
SL061RAWE: 6677.0
SL062RGAR: 7872.0
SL063REPL: 7116.0
SL064DSME: 1676.0
SL064RBLO: 5721.0
SL065RUND: 3121.0
SL066DCAR: 3317.0
SL067DZIT: 4139.0
SL067RDOD: 4559.0
SL068DSEY: 1525.0
SL068RBUT: 3207.0
SL069DCRE: 2556.0
SL069RSAN: 4747.0
SL070RHIL: 7460.0
SL071RHOW: 7096

### Rules and Regulations

In [130]:
rules_csv_path = './2022-General-Election-Constitutional-Amendment-Question-1-Rules-and-Regulations-Results-By-Precinct.xlsx'
rules_results = pd.read_excel(rules_csv_path)
rules_results

County                                       Precinct  \
0            Allen                               Carlyle Township   
1            Allen                               Carlyle Township   
2            Allen                         Cottage Grove Township   
3            Allen                         Cottage Grove Township   
4            Allen                            Deer Creek Township   
5            Allen                            Deer Creek Township   
6            Allen                                       East Elm   
7            Allen                                       East Elm   
8            Allen                                Geneva Township   
9            Allen                                Geneva Township   
10           Allen                              Humboldt Township   
11           Allen                              Humboldt Township   
12           Allen                Humboldt Township Rural Enclave   
13           Allen                Humboldt Township Rural Enclave   
14           Allen                        Humboldt Township Split   
15           Allen                        Humboldt Township Split   
16           Allen             Humboldt Township Rural Enclave 2x   
17           Allen             Humboldt Township Rural Enclave 2x   
18           Allen                                Humboldt Ward 1   
19           Allen                                Humboldt Ward 1   
20           Allen                                Humboldt Ward 2   
21           Allen                                Humboldt Ward 2   
22           Allen                                 Logan Township   
23           Allen                                 Logan Township   
24           Allen                              Marmaton Township   
25           Allen                              Marmaton Township   
26           Allen                                  North Elsmore   
27           Allen                                  North Elsmore   
28           Allen                              North Iola Part A   
29           Allen                              North Iola Part A   
30           Allen                              North Iola Part B   
31           Allen                              North Iola Part B   
32           Allen                                 Osage Township   
33           Allen                                 Osage Township   
34           Allen                                 Salem Township   
35           Allen                                 Salem Township   
36           Allen                                  South Elsmore   
37           Allen                                  South Elsmore   
38           Allen                                     South Iola   
39           Allen                                     South Iola   
40           Allen                             South Iola Enclave   
41           Allen                             South Iola Enclave   
42           Allen                           Bassett City Enclave   
43           Allen                           Bassett City Enclave   
44           Allen                                       West Elm   
45           Allen                                       West Elm   
46           Allen                                    Iola Ward 1   
47           Allen                                    Iola Ward 1   
48           Allen                                    Iola Ward 2   
49           Allen                                    Iola Ward 2   
50           Allen                                    Iola Ward 3   
51           Allen                                    Iola Ward 3   
52           Allen                            Iola Ward 3 Enclave   
53           Allen                            Iola Ward 3 Enclave   
54           Allen                            Iola Ward 3 Exclave   
55           Allen                            Iola Ward 3 Exclave   
56           Allen                                    Iola Ward 4   
57        